This Jupyter notebook will use the SEAScope viewer and SEAScope Python bindings to retrieve inputs data
* author: Lucile Gaultier, OceanDataLab
* date: 2022-10-12

To install SEAScope, follow the instructions on the [SEAScope website](https://seascope.oceandatalab.com/) and demonstrated in our ["SEAScope How To" YouTube playlist](https://www.youtube.com/playlist?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK).

To install the required Python packages, follow the instructions on https://pypi.org/project/SEAScope-env-OTC2023.
* **Windows** users can also follow the [Complete SEAScope install with Python modules for OTC23 on Windows](https://youtu.be/uomHRQPgqb8?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=3&t=132s) video on YouTube
* **macOS** users can also follow the [Installing SEAScope Python modules for OTC23 on macOS](https://youtu.be/w5f0ow6iPOY?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=6) video on YouTube

# Study of the correlation / anti-correlation between SST and Chlorophyll

Sentinel-3 data are great to perform SLSTR SST and OLCI Chlorophyll comparison as both sensors are onboard this satellite and thus collocated in time.

We know that inside cyclonic eddies and in upwelling events, vertical velocity is bringing water to the surface. This water is usually cold and rich in biogeochemistry meaning that we have an anti-correlation between SST and Chlorophyll.

This notebook will teach you how to:
* Import data from SEAScope
* Export data to SEAScope
* Investigate correlation between SST and Chlorophyll

<div class="alert alert-warning">
<strong>This notebook uses the following data collections:</strong>

* directory: `sentinel3_olci_l2_wfr`, label: `sentinel3 olci l2 wfr`
* directory: `sentinel3_slstr_l1_bt`, label: `sentinel3 slstr l1 bt`

Check that you have them in your SEAScope catalogue before continuing with this notebook.<br>
These collections can be downloaded at https://ftp.odl.bzh/events/otc23/data_ilb7.zip

To learn how to add data to SEAScope, you can watch one of the following YouTube videos:
* [How to add data to SEAScope on **Windows**](https://youtu.be/TsJSg7V7WNU?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=2)
    * or the "Add data to SEAScope" chapter of [How to add data to SEAScope on **Windows**](https://youtu.be/uomHRQPgqb8?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=3&t=40s)
* [How to add data to SEAScope on **macOS**](https://youtu.be/s5X3ewpmcuw?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=5)
* [How to add data to SEAScope on **Linux**](https://youtu.be/3ZAzgl3v2lo?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=8)
</div>

In [ ]:
# Import necessary module
%matplotlib inline
import matplotlib.pyplot as plt
import numpy
import os
from scipy import ndimage

# Create once the collection for this notebook
collection_id = None
import SEAScope.lib.utils
SEAScope.lib.utils.init_ids(72, 7120)

## 1. Define mathematical functions that will be used to compare Chlorophyll and SST

* Covariance: $C(X, Y) = E[(X-E[X])(Y-E[Y])]$ with $E$ the [expected value](https://en.wikipedia.org/wiki/Expected_value)
* Average: $A(X) = E[X]$ with $E$ the [expected value](https://en.wikipedia.org/wiki/Expected_value)
* Correlation: $r(X, Y) = \frac{C(X, Y)}{\sigma (X) \sigma (Y)}$ with $\sigma$ the [standard deviation](https://en.wikipedia.org/wiki/Standard_deviation)

In [ ]:
def covariance(x, y, size=(21, 21)):
    kernel = numpy.ones(size, dtype=bool)
    cov = (
        ndimage.convolve(x * y, kernel) / kernel.size
        - ndimage.convolve(x, kernel) * ndimage.convolve(y, kernel) / kernel.size ** 2
    )
    return cov

def average(x, size=(21, 21)):
    kernel = numpy.ones(size, dtype=bool)
    avg = ndimage.convolve(x, kernel) / kernel.size
    return avg

def correlation(x, y, size=(21, 21)):
    cov = covariance(x, y, size)

    stdx = numpy.sqrt(abs(covariance(x, x, size)))
    stdx = numpy.ma.masked_equal(stdx, numpy.nan)

    stdy = numpy.sqrt(abs(covariance(y, y, size)))
    stdy = numpy.ma.masked_equal(stdy, numpy.nan)

    corr = cov / (stdx * stdy)
    corr_mask = average(x.mask | y.mask, size) > 0
    corr = numpy.ma.array(corr, mask=corr_mask)

    return corr

## 2. Find the data of interest in SEAScope

##### Select and locate the data in the SEAScope viewer

1. In the "Catalogue" (the panel on the right), select both:
    * collection `sentinel3 olci l2 wfr`, variable `Chlorophylla_OC4ME`
    * collection `sentinel3 slstr l1 bt`, variable `SST`
2. Pick a date where you have both data available (highlighted in green in the timeline)
    * The 20<sup>th</sup> of September 2022 should be good
3. Locate the data on the globe
    * It should be in the Agulhas region

##### Compare the Chlorophyll and SST visually

Try changing the transparency of `sentinel3 slstr l1 bt: SST` in the "Display data" panel to compare Chlorophyll and SST

Notice the minimum of temperature and maximum of Chlorophyll inside cyclonic eddies

## 3. Get data from the SEAScope viewer using the python bindings

##### Extract the data from SEAScope

1. Zoom-in to properly see the structures in the data (the resolution of the extraction depends on the zoom level)
2. Draw a polygon over the region you want to extract:
    1. Start drawing by clicking on the 3<sup>rd</sup> button to the right of the pen icon in the toolbar or by hitting the <kbd>P</kbd> key
    2. Place the corners of the polygon by left-clicking on the globe
    3. Once all the corners placed, hit the <kbd>Enter</kbd> or <kbd>Return</kbd> key to commit your polygon
3. Select the polygon you just created by clicking on it
4. Extract the data intersecting that polygon by clicking on the extract button in the "Selected annotation" panel

You can also watch the [How to export data from SEAScope](https://youtu.be/jN-67nwWbUA) video on YouTube.

##### Load the extracted data

In [ ]:
# Load data from the viewer's memory
from SEAScope.lib import get_extracted_data
extractions = get_extracted_data()

# Sort extracted granules by ascending time
time_sorted_extractions = dict(sorted(extractions.items(), key=lambda _: _[1]['meta']['start']))

##### Identify Sentinel-3 Chlorophyll and SST extracted granules

In [ ]:
# Keep a list of indices for granules whose name matches the Sentinel-3 Chlorophyll or the SST data
k_chl = []
k_sst = []
for k, (granule_path, granule_info) in enumerate(time_sorted_extractions.items()):
    granule_name = os.path.basename(granule_path)
    if 'OL_2_WFR' in granule_name:
        k_chl.append(k)
    elif 'SL_1_RBT' in granule_name:
        k_sst.append(k)

    # Print extracted granule data 
    print(f'{k} - {granule_name}')
    print('\n'.join([f'\t{_}' for _ in granule_info['data']]))

if len(k_sst) == 0:
    print('Wrong collections selected, go back to SEAScope and select "sentinel3 slstr l1 bt" collection, variable SST')
if len(k_chl) == 0:
    print('Wrong collections selected, go back to SEAScope and select "sentinel3 olci l2 wfr" collection, variable Chlorophylla_OC4ME')

##### Select the granules to analyze

In [ ]:
# If several granules have been selected, select the one you want to process
kt = 0 # ⚠️ You can adapt if you have several granules imported

granule_names_list = list(time_sorted_extractions.keys())
granule_chl =  granule_names_list[k_chl[kt]]
granule_sst =  granule_names_list[k_sst[kt]]

extraction_chl = time_sorted_extractions[granule_chl]
extraction_sst = time_sorted_extractions[granule_sst]

data_chl = extraction_chl['data']['CHL_OC4ME']
data_sst = extraction_sst['data']['sea_surface_temperature']
mask_data = (numpy.ma.getmaskarray(data_chl) | numpy.ma.getmaskarray(data_sst))

# Make sure the result is reset
granule_id = None

## 4. Plot SST and Chlorophyll variables

In [ ]:
plt.figure(figsize=(6.4 * 2, 4.8))
plt.subplot(1, 2, 1)
plt.pcolormesh(data_chl, cmap='jet')
plt.colorbar()
plt.title('S3 OLCI Chlorophyll-a OC4ME')

plt.subplot(1, 2, 2)
plt.pcolormesh(data_sst, cmap='jet')
plt.colorbar() 
plt.title('S3 SLSTR SST')

##### Scatter plots between two variables represent well their relation

In [ ]:
plt.scatter(data_chl[~mask_data], data_sst[~mask_data])
plt.xlabel('Chlorophyll')
plt.ylabel('SST')
plt.title('Chlorophyll - SST')

## 5. Compute correlation between SST and Chlorophyll and plot it

$R(SST, Chl) = \frac{C(SST, Chl)}{\sigma(SST) \sigma(Chl)}$
* $R$ is the correlation
* $C$ is the covariance
* $\sigma$ is the standard deviation

##### <span style="color:red"><b>Choose the size of the kernel for your correlation</b></span>

In [ ]:
kernel_size = (17, 17) # ⚠️ You can adapt the size of the kernel to compute correlation

##### Compute the correlation matrix $R$

In [ ]:
correlation_mat = correlation(data_sst, data_chl, size=kernel_size)

##### Plot the correlation matrix $R$

In [ ]:
plt.pcolor(correlation_mat, vmax=1, vmin=-1, cmap='jet')
plt.colorbar()
plt.title('Correlation between SST and Chorophyll')

## 6. Export data back to SEAScope

In [ ]:
import json
import datetime

from SEAScope.lib.utils import create_collection, create_variable
from SEAScope.lib.utils import create_granule, set_field

**Define Collection: <br>
A granule has to belong to a collection<br>
<span style="color:red">You may choose a name for the collection `collection_name`</span>**

In [ ]:
if collection_id is None:
    # Collection
    collection_name = 'User - Correlation' # ⚠️ You can choose your collection name
    # Create collection
    collection_id, collection = create_collection(collection_name)
print(collection_id)

**Define the granule that will hold the results. Granules are defined by their spatial and temporal coverage**

In [ ]:
# Reuse the temporal coverage of the Chlorophyll-a input granule
# - Start time of granule 
dtstart = extraction_chl['meta']['start']
# - End time of granule 
dtstop = extraction_chl['meta']['stop']

# Spatial coverage will be the mesh of the polygon used to perform the extraction
# It is available in the "gcps" metadata for each extraction
gcps = extraction_chl['meta']['gcps'] 

# Create granule
if granule_id is None:
    granule_id, granule = create_granule(collection_id, gcps, dtstart, dtstop)

**The granule will contain each result matrix as what we call a "field"<br>
<span style="color:red">You may choose a name for the field `field_name`</span>**

In [ ]:
# Attach data fields to the granule
field_name = f'correlation_{kernel_size[0]}' # ⚠️ You can choose your field name
set_field(granule, field_name, correlation_mat)

**Next you need to tell SEAScope what to display: this is done by defining a "variable" which can be composed of
one, two or three fields. <br />
When a variable has two fields, these are considered to be the meridional and zonal components of a vector field.** <br>
**<span style="color:red"> You may choose a name for each variable you want to display `variable_name`</span>**</br>

In [ ]:
# Create a variable for the correlation
variable_name = field_name  # ⚠️ You can choose your label name
tmp = create_variable(collection, variable_name, [field_name])
if tmp is not None:
    variable = tmp
else:
    print()
    raise Exception('See issues above')

**It is also possible to tell SEAScope how to display variables: the following cell shows how to set some rendering options**

In [ ]:
# Rendering configuration for the output data
v_rcfg = variable['rendering']
v_rcfg['min'] = -1
v_rcfg['max'] = 1
v_rcfg['colormap'] = 'doppler'

**Finally, send the collection, granule and variable to SEAScope**

In [ ]:
hostname = '127.0.0.1'
port = 11155
with SEAScope.upload.connect(hostname, port) as link:
    # Upload the collection first (remember: a granule cannot exist before its collection has been uploaded!)
    SEAScope.upload.collection(link, collection)

    # Then the granule
    SEAScope.upload.granule(link, granule)

    # Now SEAscope has access to the data, all that remains is telling the application what and how it should display them, by uploading the variable definition
    SEAScope.upload.variable(link, variable)
    SEAScope.upload.rendering_config(link, v_rcfg)

## 7. Visualize your correlation in the SEAScope viewer

Your new collection should have appeared in the "Catalogue"
* Your collection is the `collection_name` you have defined previously
* Your variable is the `variable_name` you have defined previously
* Select the data you have just exported
* Play with transparency to check areas of correlation / anti-correlation

**You can still change the rendering configuration using the notebook, just remember to send the modified configuration to SEAScope <br />
<span style="color:red"> You can play with min, max values, the colormap ... and check how the rendering changes on SEAScope</span>**

In [ ]:
v_rcfg['min'] = -0.8
v_rcfg['max'] = 0.8
v_rcfg['colormap'] = 'doppler'

with SEAScope.upload.connect(hostname, port) as link:
    SEAScope.upload.rendering_config(link, v_rcfg)